
# Assign modes in activation maps to brain regions

Statistical parcellations maps can also assign regions to image volumes. If
given a ``Nifti1Image`` object as input, the assignment method will interpret
it as a measurement of a spatial distribution. It will first split the image
volume into disconnected components, i.e. any subvolumes which are clearly
separated by zeros. Then, each component will be compared to each statistical
maps in the same way that the Gaussian blobs representing uncertain points are
processed in `sphx_glr_examples_05_anatomical_assignment_001_coordinates.py`.

We start again by selecting the Julich-Brain probabilistic maps from
the human atlas, which we will use for the assignment.


In [ ]:
import siibra
from nilearn import plotting

Select a probabilistic parcellation map to do the anatomical assignments.



In [ ]:
julich_pmaps = siibra.get_map(
    parcellation="julich 2.9",
    space="mni152",
    maptype="statistical"
)

As an exemplary input signal, we use a  statistical map from the 64-component
functional mode parcellation (DiFuMo 64) by Thirion et al.



In [ ]:
difumo_maps = siibra.get_map(
    parcellation='difumo 64',
    space='mni152',
    maptype='statistical'
)
region = "fusiform posterior"
img = difumo_maps.fetch(region=region)

# let's look at the resulting query image
plotting.view_img(
    img,
    symmetric_cmap=False,
    cmap="magma"
)

This "fake functional map" has two modes, one in each hemisphere. We now
assign cytoarchitectonic regions to this functional map. Since we are here
usually interested in correlations of the modes, we filter the result by
significant (positive) correlations.
To assigne an image, we first need to createa Volume which has to have a
space defined.



In [ ]:
volume = siibra.volumes.volume.from_nifti(img, difumo_maps.space, "fusiform posterior")
with siibra.QUIET:  # suppress progress output
    assignments = julich_pmaps.assign(volume)
assignments.query('correlation >= 0.35')